In [95]:
import pandas as pd
import numpy as np
import nltk
import spacy
import unidecode
from word2number import w2n
import contractions
import unicodedata
pd.set_option('display.width',1000)
pd.set_option('max_colwidth', 1000) 

In [96]:
from bs4 import BeautifulSoup
from nltk.corpus import stopwords
stpwrds = set(stopwords.words('english'))
stpwrds.discard('not')
stpwrds.discard('no')
import spacy
nlp = spacy.load('en_core_web_sm')

In [3]:
%cd "C:/BEPEC Python Material\NLP (spam-project)"

C:\BEPEC Python Material\NLP (spam-project)


In [97]:
df = pd.read_csv('NB.csv' , encoding = 'ISO-8859-1')
df.head()

type                                                                                                                                                               text
0   ham                                                                                                                  Hope you are having a good week. Just checking in
1   ham                                                                                                                                            K..give back my thanks.
2   ham                                                                                                                        Am also doing in cbe only. But have to pay.
3  spam             complimentary 4 STAR Ibiza Holiday or å£10,000 cash needs your URGENT collection. 09066364349 NOW from Landline not to lose out! Box434SK38WP150PPM18+
4  spam  okmail: Dear Dave this is your final notice to collect your 4* Tenerife Holiday or #5000 CASH award! Call 09061743806 from landline. TCs SAE Box326 CW25WX 150ppm

In [98]:
df['type'].replace(to_replace=['ham','spam'], value=[0,1], inplace=True)
df.head()

type                                                                                                                                                               text
0     0                                                                                                                  Hope you are having a good week. Just checking in
1     0                                                                                                                                            K..give back my thanks.
2     0                                                                                                                        Am also doing in cbe only. But have to pay.
3     1             complimentary 4 STAR Ibiza Holiday or å£10,000 cash needs your URGENT collection. 09066364349 NOW from Landline not to lose out! Box434SK38WP150PPM18+
4     1  okmail: Dear Dave this is your final notice to collect your 4* Tenerife Holiday or #5000 CASH award! Call 09061743806 from landline. TCs SAE Box326 CW25WX 150ppm

In [55]:
df['type'].value_counts()

0    4812
1     747
Name: type, dtype: int64

## First trying on sample data

In [87]:
## For removing HTML tags using beautiful soup
def strip_html_tags(text):
    """remove html tags from text"""
    soup = BeautifulSoup(text, "html.parser")
    stripped_text = soup.get_text(separator=" ")
    return stripped_text

## For removing Accented characters
def remove_accented_chars(text):
    """remove accented characters from text, e.g. café"""
    #text = unidecode.unidecode(text)
    text = unicodedata.normalize('NFKD', text).encode('ascii', 'ignore').decode('utf-8', 'ignore')
    return text

## Removing contractions
def expand_contractions(text):
    """expand shortened words, e.g. don't to do not"""
    text = contractions.fix(text)
    return text

## Word to number(optional not much nesseceray)
text = """three cups of coffee to 3 cups of coffee"""
doc = nlp(text)
tokens = [w2n.word_to_num(token.text) if token.pos_ == 'NUM' else token for token in doc]
print(tokens)

## Removing specaill characters
def remove_special_characters(text):
    text = re.sub('[^a-zA-z0-9\s]', '', text)
    return text

# Extra white spaces
def remove_whitespace(text):
    """remove extra whitespaces from text"""
    text = text.strip()
    return " ".join(text.split())

def lemmatize_text(text):
    text = nlp(text)
    text = ' '.join([word.lemma_ if word.lemma_ != '-PRON-' else word.text for word in text])
    return text

def remove_stopwords(text, is_lower_case=False):
    tokens = nltk.word_tokenize(text)
    tokens = [token.strip() for token in tokens]
    if is_lower_case:
        filtered_tokens = [token for token in tokens if token.lower() not in stpwrds]
    else:
        filtered_tokens = [token for token in tokens if token.lower() not in stpwrds]
    filtered_text = ' '.join(filtered_tokens)    
    return filtered_text

[3, cups, of, coffee, to, 3, cups, of, coffee]


In [88]:
"""
nlp = spacy.load('en_core_web_sm')
spacy_stopwords = spacy.lang.en.stop_words.STOP_WORDS
# exclude words from spacy stopwords list
deselect_stop_words = ['no', 'not']
for w in deselect_stop_words:
    nlp.vocab[w].is_stop = False
spacy_stopwords_2 = spacy.lang.en.stop_words.STOP_WORDS
print(len(spacy_stopwords) , len(spacy_stopwords_2))
"""

"\nnlp = spacy.load('en_core_web_sm')\nspacy_stopwords = spacy.lang.en.stop_words.STOP_WORDS\n# exclude words from spacy stopwords list\ndeselect_stop_words = ['no', 'not']\nfor w in deselect_stop_words:\n    nlp.vocab[w].is_stop = False\nspacy_stopwords_2 = spacy.lang.en.stop_words.STOP_WORDS\nprint(len(spacy_stopwords) , len(spacy_stopwords_2))\n"

In [89]:
spacy_stopwords

NameError: name 'spacy_stopwords' is not defined

In [103]:
def normalize_doc(doc, html_stripping=True, contraction_expansion=True,
                     accented_char_removal=True, text_lower_case=True, 
                     text_lemmatization=True, special_char_removal=True, 
                     stopword_removal=True):
    normalized_document = []
    # strip HTML
    if html_stripping:
        doc = strip_html_tags(doc)
    # remove accented characters
    if accented_char_removal:
        doc = remove_accented_chars(doc)
    # expand contractions    
    if contraction_expansion:
        doc = expand_contractions(doc)
    # lowercase the text    
    if text_lower_case:
        doc = doc.lower()
    # remove extra newlines
    doc = re.sub(r'[\r|\n|\r\n]+', ' ',doc)
    # lemmatize text
    if text_lemmatization:
        doc = lemmatize_text(doc)
    # remove special characters    
    if special_char_removal:
        doc = remove_special_characters(doc)
    # remove extra whitespace
    doc = re.sub(' +', ' ', doc)
    # remove stopwords
    if stopword_removal:
        doc = remove_stopwords(doc, is_lower_case=text_lower_case)
    normalized_document.append(doc)
    return doc

In [91]:
## Just for practice above concepts
text = "  hi this Ali\n and hope so you're well\n\n\n we are   going\n\nto\tlahoe"
doc = re.findall(r'[\r|\n|\t]+',text)
print(doc)
special_char_pattern = re.compile(r'([{.(-)!}])')
text2 = r'AV analytics!** in (in)-dia@'
abc = special_char_pattern.sub(" \\1",text2)
abc

<IPython.core.display.Javascript object>

['\n', '\n\n\n', '\n\n', '\t']


<IPython.core.display.Javascript object>

'AV analytics !** in  (in )-dia@'

In [92]:
## Just for practice above concepts
re.sub(r' +',' ',text)

<IPython.core.display.Javascript object>

" hi this Ali\n and hope so you're well\n\n\n we are going\n\nto\tlahoe"

In [104]:
document = """<p>Héllo! Héllo! can you hear me! I just heard about <b>Python</b>!<br/>\r\n 
              It's an amazing language which can be used for Scripting, Web development,\r\n\r\n
              Information Retrieval, Natural Language Processing, Machine Learning & Artificial Intelligence!\n
              What are you waiting for? Go and get started.<br/> He's learning, she's learning, they've already\n\n
              got a headstart!</p>
           """
document

"<p>Héllo! Héllo! can you hear me! I just heard about <b>Python</b>!<br/>\r\n \n              It's an amazing language which can be used for Scripting, Web development,\r\n\r\n\n              Information Retrieval, Natural Language Processing, Machine Learning & Artificial Intelligence!\n\n              What are you waiting for? Go and get started.<br/> He's learning, she's learning, they've already\n\n\n              got a headstart!</p>\n           "

In [105]:
normalize_doc(document)

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

'hello hello hear hear python amazing language use scripting web development information retrieval natural language processing machine learning artificial intelligence wait go get start learn learn already get headstart'

In [106]:
document = "okmail: Dear Dave this is your final notice to collect your 4* Tenerife Holiday or #5000 CASH award! Call 09061743806 from landline. TCs SAE Box326 CW25WX 150ppm"
document

'okmail: Dear Dave this is your final notice to collect your 4* Tenerife Holiday or #5000 CASH award! Call 09061743806 from landline. TCs SAE Box326 CW25WX 150ppm'

In [107]:
normalize_doc(document)

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

'okmail dear dave final notice collect 4 tenerife holiday 5000 cash award call 09061743806 landline tcs sae box326 cw25wx 150ppm'

In [108]:
## it will take a few minutes (5-7mins)
df['Clean_text'] = df['text'].apply(normalize_doc)
df.sample(10)

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

...

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

type                                                                                                                                                                                 text                                                                                                                                Clean_text
207      0                                                                       hope things went well at 'doctors' ;) reminds me i still need 2go.did u c d little thing i left in the lounge?                                                            hope thing go well doctor remind still need 2godid c little thing leave lounge
5532     1                                            Sunshine Quiz Wkly Q! Win a top Sony DVD player if u know which country Liverpool played in mid week? Txt ansr to 82277. å£1.50 SP:Tyrone                           sunshine quiz wkly q win top sony dvd player know country liverpool play mid week txt ansr 82277 a150 sp tyrone
5386     0                                                                                                                                                      Dear umma she called me now :-)                                                                                                                            dear umma call
1052     0                                                                                                                                           Ic. There are a lotta childporn cars then.                                                                                                                    ic lotta childporn car
4115     0                                                                    Oh thats late! Well have a good night and i will give u a call tomorrow. Iam now going to go to sleep night night                                                                    oh late well good night give call tomorrow iam go go sleep night night
2132     0  Wen ur lovable bcums angry wid u, dnt take it seriously.. Coz being angry is d most childish n true way of showing deep affection, care n luv!.. kettoda manda... Have nice day da.  wen ur lovable bcum angry wid dnt take seriously coz angry childish n true way show deep affection care n love kettoda manda nice day da
913      0                                                                                    This pen thing is beyond a joke. Wont a Biro do? Don't do a masters as can't do this ever again!                                                                                         pen thing beyond joke not biro not master not ever
996      0                                                                                                                                               S'fine. Anytime. All the best with it.                                                                                                                        sfine anytime good
3153     0                                                                                                                                                              No management puzzeles.                                                                                                                     no management puzzele
1837     0                                                                                                                                                          I uploaded mine to Facebook                                                                                                                      upload mine facebook